In [ ]:
import numpy as np
from numpy import linalg
import numpy.matlib 
import matplotlib.pyplot as plt
from IPython.display import clear_output
from time import sleep
from scipy.signal import sepfir2d
from scipy import ndimage

In [ ]:
# 7-frame motion estimation

# load images
for j in range(1,2):
    vid = []; 
    for k in range(1,8):
        img = plt.imread("./motionTaxi/taxi" + str(k+j).zfill(2) + ".pgm" ) # image indexing starts at 1
        if( len(img.shape) == 3 ):
            vid.append( 1.0*img[:,:,2] ) # extract green channel
        else:
            vid.append( 1.0*img ) # already grayscale

    # compute space-time derivatives
    p = [0.005165, 0.068654, 0.244794, 0.362775, 0.244794, 0.068654, 0.005165] # prefilter
    d = [-0.018855, -0.123711, -0.195900, 0.0, 0.195900, 0.123711, 0.018855] # derivative

    ydim,xdim = vid[0].shape
    fdt = np.zeros((ydim,xdim))
    fpt = np.zeros((ydim,xdim))
    for k in range(7):
        fdt = fdt + d[6-k]*vid[k] # differentiate in time
        fpt = fpt + p[6-k]*vid[k] # prefilter in time

    fx  = sepfir2d( fpt, d, p ) # spatial (x) derivative
    fy  = sepfir2d( fpt, p, d ) # spatial (y) derivative
    ft  = sepfir2d( fdt, p, p ) # temporal derivative

    h   = [1/16,4/16,6/16,4/16,1/16] # spatial averaging
    fx2 = sepfir2d( fx*fx, h, h )
    fy2 = sepfir2d( fy*fy, h, h )
    fxy = sepfir2d( fx*fy, h, h )
    fxt = sepfir2d( fx*ft, h, h )
    fyt = sepfir2d( fy*ft, h, h )

    # compute motion (at every other pixel)
    Vx = np.zeros((ydim//2,xdim//2))
    Vy = np.zeros((ydim//2,xdim//2))
    cx = 0
    for x in range(0,xdim-1,2):
        cy = 0
        for y in range(0,ydim-1,2):
            # build linear system
            M = [[fx2[y,x], fxy[y,x]], [fxy[y,x], fy2[y,x]]]
            b = [[fxt[y,x]], [fyt[y,x]]]
            
            # well-conditioned matrix and large gradient
            if( linalg.cond(M)<1e2 and (np.sqrt(fx[y,x]*fx[y,x]+fy[y,x]*fy[y,x])>2) ): 
                v = -linalg.inv(M)@b # least-squares solution
                Vx[cy,cx] = v[0]
                Vy[cy,cx] = v[1]
            cy = cy + 1
        cx = cx + 1

    # display motion
    plt.figure(figsize=(4*xdim/72,4*ydim/72))
    plt.imshow( vid[3], cmap='gray' )
    Ny,Nx = vid[0].shape
    X,Y = np.meshgrid(np.arange(0,Nx-1,2),np.arange(0,Ny-1,2))
    Vx = ndimage.median_filter(Vx, size=5) # remove outliers
    Vy = ndimage.median_filter(Vy, size=5) # remove outliers
    Vy = -1*Vy # flipped y-axis

    _ = plt.quiver(X,Y,Vx,Vy,scale=50,color='y',alpha=0.8, width=0.002, minlength=0)
    plt.axis('off')
    plt.show()
    sleep(0.01)
    clear_output(wait=True)

In [ ]:
# 2-frame motion estimation

import numpy as np
import numpy.matlib 
import matplotlib.pyplot as plt
from numpy import linalg
from scipy.signal import sepfir2d
from scipy import ndimage

# load images
vid = []
vid.append( 1.0*plt.imread("./motionTaxi/taxi01.pgm") )
vid.append( 1.0*plt.imread("./motionTaxi/taxi02.pgm") ) 

# compute space-time derivatives
# these filters should be [1/5, 1/5] and [-1, 1], but sepfir2d requires odd-length filters
p   = [1/3, 1/3, 1/3] # prefilter
d   = [-1, 0, 1] # derivative filter

fx  = sepfir2d( 0.5*vid[0]+0.5*vid[1], d, p ) # spatial(x) derivative
fy  = sepfir2d( 0.5*vid[0]+0.5*vid[1], p, d ) # spatial(y) derivative
ft  = sepfir2d( vid[0]-vid[1], p, p ) # temporal derivative

h   = [1/16,4/16,6/16,4/16,1/16] # spatial averaging
fx2 = sepfir2d( fx*fx, h, h )
fy2 = sepfir2d( fy*fy, h, h )
fxy = sepfir2d( fx*fy, h, h )
fxt = sepfir2d( fx*ft, h, h )
fyt = sepfir2d( fy*ft, h, h )

# compute motion (at every other pixel)
ydim,xdim = vid[0].shape
Vx = np.zeros((ydim//2,xdim//2))
Vy = np.zeros((ydim//2,xdim//2))
cx = 0
for x in range(0,xdim-1,2):
    cy = 0
    for y in range(0,ydim-1,2):
        # build linear system
        M = [[fx2[y,x], fxy[y,x]], [fxy[y,x], fy2[y,x]]]
        b = [[fxt[y,x]], [fyt[y,x]]]
        
        # well-conditioned matrix and large gradient
        if( linalg.cond(M)<1e2 and 
           (np.sqrt(fx[y,x]*fx[y,x]+fy[y,x]*fy[y,x])>2) ): 
            v = -linalg.inv(M)@b # least-squares solution for motion
            Vx[cy,cx] = v[0] 
            Vy[cy,cx] = v[1]
        cy = cy + 1
    cx = cx + 1

# display motion
plt.figure(figsize=(4*xdim/72,4*ydim/72))
plt.imshow( vid[0], cmap='gray' )
Ny,Nx = vid[0].shape
X,Y   = np.meshgrid(np.arange(0,Nx-1,2),np.arange(0,Ny-1,2))
Vx    = ndimage.median_filter(Vx, size=5) # remove outliers
Vy    = ndimage.median_filter(Vy, size=5) # remove outliers
Vy    = -1*Vy # flipped y-axis

_ = plt.quiver(X,Y, Vx,Vy, scale=50, color='y', 
               alpha=0.8, width=0.002, minlength=0)
plt.axis('off')
plt.show()

In [ ]:
# 2-frame feature-based motion estimation
import numpy as np
import numpy.matlib 
import matplotlib.pyplot as plt
from numpy import linalg
from scipy.signal import sepfir2d
from scipy import ndimage

# load images
vid = []
vid.append( 1.0*plt.imread("./motionTaxi/taxi01.pgm") )
vid.append( 1.0*plt.imread("./motionTaxi/taxi02.pgm") ) 

# compute motion (at every fourth pixel)
ydim,xdim = vid[0].shape
Vx = np.zeros((ydim//4+1,xdim//4+1))
Vy = np.zeros((ydim//4+1,xdim//4+1))
sz = 5 # block size: (2*sz+1) x (2*sz+1) pixels
cx = 0
for x in range(0,xdim,4):
    cy = 0
    for y in range(0,ydim,4):
        if( x-sz>=0 and x+sz<xdim and y-sz>=0 and y+sz<ydim ):
            blk1 = vid[0][y-sz:y+sz,x-sz:x+sz] # block from frame 1
            mindiff = 1e10
            for u in range(x-10,x+10):
                for v in range(y-10,y+10):
                    if( u-sz>=0 and u+sz<xdim and v-sz>=0 and v+sz<ydim ):
                        blk2 = vid[1][v-sz:v+sz,u-sz:u+sz] # block from frame 2
                        diff = np.abs(blk1-blk2) # block difference
                        diffval = np.sum(diff.flatten()) # sum of abs differences
                        if( diffval < mindiff ):
                            mindiff = diffval # found better match
                            Vx[cy,cx] = u-x   #
                            Vy[cy,cx] = v-y   # 
        cy = cy + 1
    cx = cx + 1
    
# remove outliners
Vx = ndimage.median_filter(Vx, size=5)
Vy = ndimage.median_filter(Vy, size=5)

In [ ]:
# display motion
plt.figure(figsize=(4*xdim/72,4*ydim/72))
plt.imshow( vid[1], cmap='gray' )
Ny,Nx = Vx.shape
X,Y   = np.meshgrid(np.arange(0,Nx),np.arange(0,Ny))
Vy    = -Vy

_ = plt.quiver(4*X,4*Y, Vx,Vy, scale=50, color='y', 
               alpha=0.8, width=0.002, minlength=0)
plt.axis('off')
plt.show()